In [1]:
import IJulia

# The julia kernel has built in support for Revise.jl, so this is the 
# recommended approach for long-running sessions:
# https://github.com/JuliaLang/IJulia.jl/blob/9b10fa9b879574bbf720f5285029e07758e50a5e/src/kernel.jl#L46-L51

# Users should enable revise within .julia/config/startup_ijulia.jl:
# https://timholy.github.io/Revise.jl/stable/config/#Using-Revise-automatically-within-Jupyter/IJulia-1

# clear console history
IJulia.clear_history()

# Intialize Plots w/ default fig width/height
try
  fig_width = 7
  fig_height = 5
  fig_format = :retina
  fig_dpi = 96
  # no retina format type, use svg for high quality type/marks
  if fig_format == :retina
    fig_format = :svg
  # IJulia doesn't support PDF output so use png (if the DPI 
  # remains the default of 300 then set to 96)
  elseif fig_format == :pdf
    fig_format = :png
    fig_dpi = 96
  end
  # convert inches to pixels
  fig_width = fig_width * fig_dpi
  fig_height = fig_height * fig_dpi
  using Plots
  gr(size=(fig_width, fig_height), fmt = fig_format, dpi = fig_dpi)
catch e
  # @warn "Plots init" exception=(e, catch_backtrace())
end

# Set run_path if specified
try
  run_path = ""
  if !isempty(run_path)
    cd(run_path)
  end
catch e
  @warn "Run path init:" exception=(e, catch_backtrace())
end

# don't return kernel dependencies (b/c Revise should take care of dependencies)
nothing


In [2]:
#| code-fold: true
#| output: false

using FileIO
using MeshIO

using stlProcess

using CSV
using DataFrames

using LinearAlgebra

In [3]:
#| code-fold: true
#| output: false

# local path to https://gitlab.com/orbital-debris-research/fake-satellite-dataset
dataset_path = raw"C:\Coding\fake-satellite-dataset"

folders = ["1_5U", "assembly1", "cubesat"]

df = DataFrame(;
    surface_area=Float64[],
    characteristic_length=Float64[],
    sbx=Float64[],
    sby=Float64[],
    sbz=Float64[],
    Ix=Float64[],
    Iy=Float64[],
    Iz=Float64[],
)

0×8 DataFrame

In [4]:
for path in dataset_path * "\\" .* folders
    println("Processing Path: ", path)
    Threads.@threads for file in readdir(path)
        stl = load(path * "\\" * file)
        scale = find_scale(stl)
        props = get_mass_properties(stl; scale=scale)

        eigs = eigvals(props.inertia)
        sort_index = sortperm(eigs)
        Ix, Iy, Iz = eigs[sort_index]
        sbx, sby, sbz = props.sb_values[sort_index]

        push!(
            df,
            [props.surface_area, props.characteristic_length, sbx, sby, sbz, Ix, Iy, Iz],
        )
    end
end

Processing Path: C:\Coding\fake-satellite-dataset\1_5U
Processing Path: C:\Coding\fake-satellite-dataset\assembly1
Processing Path: C:\Coding\fake-satellite-dataset\cubesat


┌ Warning: Characteristic Length Algorithm failed to converge, this usually means stl is flat. Setting length in dir to 0.
└ @ stlProcess C:\Users\albig\.julia\packages\stlProcess\8rsc7\src\stlProcess.jl:153


In [5]:
describe(df)

8×7 DataFrame
 Row │ variable               mean      min        median     max         nmis ⋯
     │ Symbol                 Float64   Float64    Float64    Float64     Int6 ⋯
─────┼──────────────────────────────────────────────────────────────────────────
   1 │ surface_area           25.2002   5.60865    13.3338     159.406         ⋯
   2 │ characteristic_length  79.5481   0.158521    1.55816   1582.23
   3 │ sbx                     1.40222  0.0417367   0.967078    10.0663
   4 │ sby                     3.3367   0.0125824   2.68461      9.68361
   5 │ sbz                     3.91184  0.29006     1.8185      14.7434        ⋯
   6 │ Ix                      1.58725  0.0311782   0.23401     11.1335
   7 │ Iy                      3.74345  0.178598    1.01592     24.6735
   8 │ Iz                      5.20207  0.178686    1.742       32.0083
                                                               2 columns omitted